## Phase 4: Council valuation dataset
### INPUTS
Council Ratings Valuation (RV) data:
-	xls file for 2011 RVs
-	xls file for 2014 RVs
-	xls file for 2017 RVs
-	xls file for 2021 RVs

### OUTPUTS
Four csv files (one for 2011, 2014, 2017 and 2021) with the following data fields added:
-	The same data fields listed through points 1-9 above under Phase 0 are to be added to each ratings valuation after each RV is matched to a parcel.
o	Naming convention: Use the same labels as given under Phase 1 (in red).


In [2]:
#pragma nodebook off
#Use nodebook for better reproducibility https://github.com/uoa-eResearch/nodebook
%reload_ext nodebook.ipython
%nodebook disk phase4

<IPython.core.display.Javascript object>

In [ ]:
# load libraries
import geopandas as gpd # vector data
import pandas as pd # tabular data, loading CSVs
import numpy as np # numeric data
from util import *
import matplotlib # plotting
import contextily as ctx # Used for contextual basemaps
from matplotlib_scalebar.scalebar import ScaleBar # scalebar for plot
import matplotlib.pyplot as plt # plotting
from tqdm.auto import tqdm # progress bars
tqdm.pandas()
import json
from scipy.spatial import cKDTree
from shapely.geometry import Point, shape, LineString, MultiLineString, GeometryCollection, MultiPoint, Polygon  # creating points
import requests
import requests_cache
requests_cache.install_cache('requests_cache')
from matplotlib_venn import venn2, venn2_circles, venn2_unweighted
from matplotlib_venn import venn3, venn3_circles
plt.rcParams['figure.figsize'] = (20, 20)
pd.set_option('display.max_columns', None)

In [ ]:
%%time
rvs = {}
for year in tqdm([2011, 2014, 2017, 2021]):
    rvs[year] = pd.read_excel(f"restricted/REVAL{year} Property Data Supply.xlsx")

  0%|          | 0/4 [00:00<?, ?it/s]

CPU times: user 11min 56s, sys: 4.29 s, total: 12min 1s
Wall time: 12min 1s


10.	Because titles can be cumbersome to work with, please add a unique numeric identifier for each RV in the dataset based on its certificate of title. Call it ‘FID_certificate_of_title’. 

In [ ]:
rvs[2021]

Valuation_Number_Roll  Valuation_Number_Assessment  \
0                        1281                        28200   
1                        3952                        52600   
2                       32200                        41117   
3                       34110                        16600   
4                       37301                        38303   
...                       ...                          ...   
593405                  32749                        19927   
593406                     16                  21230030110   
593407                    941                        39000   
593408                  31250                     12656736   
593409                  33351                        14054   

       Valuation_Number_Suffix  District_Code  Situation_Number  \
0                          NaN             14                20   
1                            B             14               789   
2                          NaN             14                16   
3                            B             14                39   
4                          NaN             14               143   
...                        ...            ...               ...   
593405                     NaN             14                 4   
593406                     NaN             14                76   
593407                     NaN             14                 6   
593408                     NaN             14                22   
593409                     NaN             14                36   

       Additional_Situation_Number      Situation_Name  \
0                              -26          Neville St   
1                              NaN            Beach Rd   
2                              NaN        Te Wharau Dr   
3                              NaN       Cliff View Dr   
4                              NaN      Great South RD   
...                            ...                 ...   
593405                         NaN        Carnelian Ct   
593406                         NaN  Stonefields Avenue   
593407                         NaN      Woods Ridge Rd   
593408                         NaN     Arran Point PDE   
593409                         NaN        Ceramic LANE   

                                       Legal_Description  Land_Area  \
0                                        Lot 1 DP 440011     0.5499   
1                                    UNIT B AU2 DP 83542     0.0000   
2                                        LOT 8 DP 196200     0.0853   
3              LOT 19 DP 39875 1/2 SH BG FLAT 2 DP 86384     0.0000   
4                                 Lot 3 DP 129805 1430m2     0.1430   
...                                                  ...        ...   
593405                                  LOT 27 DP 207011     0.0514   
593406  Lot 101 DP 466374 1138m2, Lot 40 DP 466374 123m2     0.0123   
593407                                   Lot 25 DP 82380     0.2070   
593408        Lot 2 DP 533517 7/120 Sh Lot 604 DP 501394     0.0176   
593409                                 Unit 48 DP 533897     0.0000   

       Property_Category  Ownership_Code  Current_Effective_Valuation_Date  \
0                   CRSB               2                           1062021   
1                 RF197B               1                           1062021   
2                 RD200B               1                           1062021   
3                 RF197B               0                           1062021   
4                    IVP               0                           1062021   
...                  ...             ...                               ...   
593405            RD200B               1                           1062021   
593406            RF201B               1                           1062021   
593407            RD200B               1                           1062021   
593408            RF201B               2                           1062021   
593409            RF201B               2          

In [ ]:
for rv in rvs.values():
    rv.Certificate_of_Title = rv.Certificate_of_Title.astype(str)

In [ ]:
venn3(
    [set(rv.Certificate_of_Title.str.replace("NA", "")) for rv in (rvs[2014], rvs[2017], rvs[2021])],
    set_labels = [2014, 2017, 2021]
)

In [ ]:
# The for loop above would set rv to the last element, so RV for 2021
len(rv.Certificate_of_Title), len(rv.Certificate_of_Title.unique())

(593410, 587234)

In [ ]:
all_cots = pd.concat(rv.Certificate_of_Title for rv in rvs.values()).unique()
all_cots.sort()
print(len(all_cots))
all_cots = {cot: i for i, cot in enumerate(all_cots)}

827489


In [ ]:
%%time
for rv in rvs.values():
    rv["FID_certificate_of_title"] = rv.Certificate_of_Title.progress_apply(lambda cot: all_cots[cot])

  0%|          | 0/516469 [00:00<?, ?it/s]

  0%|          | 0/529046 [00:00<?, ?it/s]

  0%|          | 0/549936 [00:00<?, ?it/s]

  0%|          | 0/593410 [00:00<?, ?it/s]

CPU times: user 13.2 s, sys: 3.82 s, total: 17 s
Wall time: 17.3 s


PROCEDURE FOR MATCHING RVs TO LINZ DATABASE  
Use certificate of title to match each valuation to a LINZ parcel(s). 

11.	Indicator for one-to-many matched LINZ parcels: ‘One_to_many_matched_parcels’  
a.	Equal to one or zero
12.	Indicator for many-to-one matched LINZ parcel: ‘Many_to_one_matched_parcels’  
a.	Equal to one or zero  

In [ ]:
%%time
parcels = gpd.read_file('input/lds-nz-primary-parcels-FGDB.zip!nz-primary-parcels.gdb').to_crs(2193).set_index("id")
addresses = gpd.read_file('input/lds-nz-addresses-pilot-FGDB.zip!nz-addresses-pilot.gdb').to_crs(2193)
def number_name_addresses(x):
    return ' '.join(x.split(' ')[:2]).lower()
addresses['address_number_name'] = addresses.full_address_ascii.apply(number_name_addresses)
parcels_addressed = gpd.sjoin(parcels, addresses)
parcels["addresses"] = parcels_addressed.groupby('id')['address_number_name'].apply(list)
parcels["full_addresses"] = parcels_addressed.groupby('id')["full_address"].apply(list)
parcels[["addresses", "full_addresses"]]

CPU times: user 2min 36s, sys: 9.35 s, total: 2min 45s
Wall time: 2min 46s


addresses  \
id                                                           
4918991  [3/12 college, 1/12 college, 2/12 college, 12 ...   
4919914                                       [15 abraham]   
4926734  [3/20 simkin, 1/20 simkin, 2/20 simkin, 20 sim...   
4926945  [3 abraham, 4/3 abraham, 3/3 abraham, 2/3 abra...   
4929034                                       [49 caulton]   
...                                                    ...   
5227472                                      [112z bairds]   
5242816                                                NaN   
7520053                                      [9 lovegrove]   
7520049                                     [15 lovegrove]   
4733845                                          [7 otara]   

                                            full_addresses  
id                                                          
4918991  [3/12 College Road, Saint Johns, Auckland, 1/1...  
4919914          [15 Abraham Place, Saint Johns, Auckland]  
4926734  [3/20 Simkin Avenue, Saint Johns, Auckland, 1/...  
4926945  [3 Abraham Place, Saint Johns, Auckland, 4/3 A...  
4929034         [49 Caulton Street, Saint Johns, Auckland]  
...                                                    ...  
5227472                [112Z Bairds Road, Ōtara, Auckland]  
5242816                                                NaN  
7520053            [9 Lovegrove Crescent, Ōtara, Auckland]  
7520049           [15 Lovegrove Crescent, Ōtara, Auckland]  
4733845                    [7 Otara Road, Ōtara, Auckland]  

[547903 rows x 2 columns]

In [ ]:
for year, rv in rvs.items():
    RV_NAs = sum(rv.Certificate_of_Title.str.contains('NA'))
    print(f"{RV_NAs} RV titles from {year} start with NA / {len(rv)} ({round(RV_NAs/len(rv)*100, 2)}%)")
parcels_NAs = sum(parcels.titles.str.contains('NA', na=False))
print(f"{parcels_NAs} parcel titles start with NA / {len(parcels)} ({round(parcels_NAs/len(parcels)*100, 2)}%)")

284487 RV titles from 2011 start with NA / 516469 (55.08%)
321794 RV titles from 2014 start with NA / 529046 (60.83%)
322573 RV titles from 2017 start with NA / 549936 (58.66%)
344471 RV titles from 2021 start with NA / 593410 (58.05%)
345003 parcel titles start with NA / 547903 (62.97%)


In [ ]:
rv.Certificate_of_Title = rv.Certificate_of_Title.str.replace("NA", "")
parcels.titles = parcels.titles.str.replace("NA","")

In [ ]:
split_titles = parcels.titles.str.split(", ").explode().dropna().str.upper()
split_titles

id
4918991      8C/911
4919914      474924
4919914      8C/768
4926734      386353
4926734      386354
             ...   
5093286    111B/230
5184362     56B/639
7520053      621250
7520049      619244
4733845     86D/103
Name: titles, Length: 723468, dtype: object

In [ ]:
print(sum(rv.Certificate_of_Title.isin(parcels.titles)))
print(sum(rv.Certificate_of_Title.str.upper().isin(parcels.titles.str.upper())))
print(sum(rv.Certificate_of_Title.str.upper().isin(split_titles)))

390137
390235
580537


In [ ]:
title_lookup = {}
for parcel_id, title in split_titles.iteritems():
    if title not in title_lookup:
        title_lookup[title] = []
    title_lookup[title].append(parcel_id)

In [ ]:
%%time
for year, rv in tqdm(rvs.items()):
    rv["matched_parcels"] = rv.Certificate_of_Title.str.replace("NA", "").str.upper().progress_apply(
        lambda t: title_lookup.get(t, [])
    )
    rv["number_of_matched_parcels"] = rv.matched_parcels.str.len()
    rv["One_to_many_matched_parcels"] = (rv.number_of_matched_parcels > 1).astype(int)
    rv["LINZ_parcel_ID"] = rv.matched_parcels.str[0]
    rv["Many_to_one_matched_parcels"] = (~pd.isna(rv.LINZ_parcel_ID) & rv.LINZ_parcel_ID.duplicated(keep=False)).astype(int)
    rvs[year] = rv

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/516469 [00:00<?, ?it/s]

  0%|          | 0/529046 [00:00<?, ?it/s]

  0%|          | 0/549936 [00:00<?, ?it/s]

  0%|          | 0/593410 [00:00<?, ?it/s]

CPU times: user 21.8 s, sys: 7.52 s, total: 29.4 s
Wall time: 30.4 s


In [ ]:
%%time
for year, rv in tqdm(rvs.items()):
    n_matched = sum(rv.number_of_matched_parcels > 0)
    print(f"{year}: {n_matched} parcels matched out of {len(rv)} ({round(n_matched/len(rv)*100,2)}%)")

  0%|          | 0/4 [00:00<?, ?it/s]

2011: 313530 parcels matched out of 516469 (60.71%)
2014: 372162 parcels matched out of 529046 (70.35%)
2017: 528203 parcels matched out of 549936 (96.05%)
2021: 580537 parcels matched out of 593410 (97.83%)
CPU times: user 11.2 s, sys: 2.67 s, total: 13.9 s
Wall time: 14.2 s


In [ ]:
rv.number_of_matched_parcels.value_counts()

1      509013
2       57038
0       12873
3        8656
4        2571
5        1338
10        544
6         400
9         305
7         263
8         206
13         69
27         46
12         39
11         13
14          7
57          3
15          3
19          3
18          3
23          2
37          2
17          2
91          1
24          1
16          1
189         1
22          1
32          1
41          1
30          1
20          1
29          1
21          1
Name: number_of_matched_parcels, dtype: int64

In [ ]:
rv.One_to_many_matched_parcels.value_counts()

0    521886
1     71524
Name: One_to_many_matched_parcels, dtype: int64

In [ ]:
rv["Many_to_one_matched_parcels"].value_counts()

0    386613
1    206797
Name: Many_to_one_matched_parcels, dtype: int64

#### Geocode the RV addresses and then follow the matching process detailed in Phase 1 for those that failed to match on title alone. Set LINZ_MATCH_CODE=0 for those that did.

In [ ]:
for year, rv in tqdm(rvs.items()):
    rv.loc[rv.number_of_matched_parcels > 0, "LINZ_MATCH_CODE"] = 0

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
rv[["Situation_Number", "Additional_Situation_Number", "Situation_Name"]].sample(20)

Situation_Number Additional_Situation_Number        Situation_Name
246215                27                         NaN          Ariki Street
148357                21                         NaN             Omana Ave
366684               123                         NaN              Owens RD
510286                 8                         NaN             Albert ST
509347                83                           1            Whitney St
471938                65                         NaN           Tiroroa AVE
96561                 16                           3            WARREN AVE
185478               192                           A             Upland RD
124660                67                           1               Rimu St
20057                 72                         NaN             Harris Dr
393094                70                           B       Estuary View Rd
128565                49                         NaN  Papakura-clevedon Rd
483444                10                         NaN           Westview Ct
263446                13                           A        Marsden Avenue
100351                 3                         NaN             Boakes RD
535823                 2                           A               Mars AV
173752               113                         NaN            Vincent ST
268804                 6                         NaN          Kahurangi Pl
446685                14                         NaN           Cityview PL
402065                10                         NaN           Bohola Rise

In [ ]:
for year, rv in tqdm(rvs.items()):
    rvs_with_addresses = rv[(rv.Situation_Number > 0) & ~pd.isna(rv.Situation_Name)].copy()
    rvs_with_addresses.Situation_Number = rvs_with_addresses.Situation_Number.astype("Int64").astype(str)
    rvs_with_addresses.Additional_Situation_Number = rvs_with_addresses.Additional_Situation_Number.replace(np.nan, "").astype(str)
    rv["full_address"] = rvs_with_addresses.Situation_Number.str.cat(
        rvs_with_addresses.Additional_Situation_Number
    ).str.cat(
        rvs_with_addresses.Situation_Name,
        sep=" "
    )
    rv["number_name"] = rv.full_address[~pd.isna(rv.full_address)].apply(lambda a: " ".join(a.lower().split()[:2]))

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
for year, rv in tqdm(rvs.items()):
    print(year, any(rv.full_address.str.contains("[āēīōū]", na=False)))

  0%|          | 0/4 [00:00<?, ?it/s]

2011 False
2014 False
2017 False
2021 False


In [ ]:
rv.LINZ_MATCH_CODE.value_counts(dropna=False)

0.0    580537
NaN     12873
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
print(sum(rv.number_name.isin(addresses.address_number_name)))
print(sum(pd.isna(rv.LINZ_MATCH_CODE) & ~pd.isna(rv.full_address)))
print(sum(rv.number_name[pd.isna(rv.LINZ_MATCH_CODE)].isin(addresses.address_number_name)))

512524
11421
8610


In [ ]:
session = requests_cache.CachedSession('requests_cache')
def geocode(address):
    url = f"https://api-proxy.auckland-cer.cloud.edu.au/nominatim/search.php"
    result = session.get(url, params={
        "q": address + ", Auckland"
    }).json()
    if result:
        return pd.Series(result[0])
    else:
        return pd.Series()
geocoding_results = {}
for year, rv in tqdm(rvs.items()):
    df = rv.full_address[pd.isna(rv.LINZ_MATCH_CODE) & ~pd.isna(rv.full_address)].progress_apply(geocode).dropna()
    df["number_name"] = rv.number_name[df.index]
    df["full_address"] = rv.full_address[df.index]
    geocoding_results[year] = df

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/199809 [00:00<?, ?it/s]

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

...

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
<string>:10: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify 

In [ ]:
df[["number_name", "full_address", "display_name"]][~df.display_name.str.contains("Auckland")]

number_name          full_address  \
27270   112 attewell       112 Attewell Rd   
78596      139c mill          139C Mill Rd   
172824      168 bald      168 Bald Hill Rd   
218522       10 bald       10 Bald Hill Rd   
292871  233 pukekohe  233 Pukekohe East Rd   
313786  57 barriball       57 Barriball Rd   
372855   97 attewell        97 Attewell Rd   
415519      115b aka       115B Aka Aka Rd   
497402    309a upper   309A Upper Queen St   

                                             display_name  
27270   112, Attewell Road, Pukekohe, Franklin, Waikat...  
78596   139C, Mill Road, Pukekohe East, Franklin, Waik...  
172824  168, Bald Hill Road, Waiuku, Franklin, Waikato...  
218522  10, Bald Hill Road, Mauku, Franklin, Waikato D...  
292871  233, Pukekohe East Road, Pukekohe East, Frankl...  
313786  57, Barriball Road, Waiuku, Franklin, Waikato ...  
372855  97, Attewell Road, Pukekohe, Franklin, Waikato...  
415519  115B, Aka Aka Road, Puni, Franklin, Waikato Di...  
497402  309A, Upper Queen Street, Pukekohe, Franklin, ...

In [ ]:
for year, df in tqdm(geocoding_results.items()):
    df = gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.lon, df.lat), crs=4326).to_crs(2193)
    df = gpd.sjoin(df, parcels[["addresses","geometry"]], how="left")
    df = df.rename(columns={"index_right": "LINZ_parcel_ID"})
    df.LINZ_parcel_ID = df.LINZ_parcel_ID.astype("Int64")
    geocoding_results[year] = df

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
%%time
def check_match(row):
    if row.number_name in row.addresses:
        return 1
for year, df in tqdm(geocoding_results.items()):
    df["LINZ_MATCH_CODE"] = df[~pd.isna(df.addresses)].apply(check_match, axis=1).dropna()
    print(f"{year}: {sum(df.LINZ_MATCH_CODE == 1)}")

  0%|          | 0/4 [00:00<?, ?it/s]

2011: 27453
2014: 21788
2017: 13349
2021: 7078
CPU times: user 7.36 s, sys: 218 ms, total: 7.58 s
Wall time: 7.6 s


In [ ]:
parcel_tree = cKDTree(list(parcels.centroid.apply(lambda x: (x.x, x.y))))
parcel_tree

In [ ]:
def find_match_in_range(row):
    indices_in_range = parcel_tree.query_ball_point([row.geometry.x, row.geometry.y], 1250)
    potential_matches = parcels.iloc[indices_in_range]
    match = potential_matches[potential_matches.addresses.str.contains(row.number_name, na=False, regex=False)]
    if len(match):
        row.LINZ_parcel_ID = match.index[0]
        row.addresses = match.addresses.iloc[0]
        row.full_addresses = match.full_addresses.iloc[0]
        row.LINZ_MATCH_CODE = 2
    return row
for year, df in tqdm(geocoding_results.items()):
    matches = df[
        ~pd.isna(df.number_name) &
        pd.isna(df["LINZ_MATCH_CODE"]) &
        df.number_name.isin(addresses.address_number_name)].progress_apply(find_match_in_range, axis=1)
    df.update(matches)

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/12405 [00:00<?, ?it/s]

  0%|          | 0/9894 [00:00<?, ?it/s]

  0%|          | 0/2239 [00:00<?, ?it/s]

  0%|          | 0/1197 [00:00<?, ?it/s]

In [ ]:
for year, df in tqdm(geocoding_results.items()):
    print(year)
    display(df.LINZ_MATCH_CODE.value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


NaN    154088
1.0     27453
2.0      2171
Name: LINZ_MATCH_CODE, dtype: int64

2014


NaN    103986
1.0     21788
2.0      1869
Name: LINZ_MATCH_CODE, dtype: int64

2017


1.0    13349
NaN     4242
2.0     1545
Name: LINZ_MATCH_CODE, dtype: int64

2021


1.0    7078
NaN    2715
2.0     821
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
%%time
number_name_lookup = {}
for parcel_id, addresses in parcels.addresses[~pd.isna(parcels.addresses)].iteritems():
    for address in addresses:
        if address not in number_name_lookup:
            number_name_lookup[address] = []
        number_name_lookup[address].append(parcel_id)

CPU times: user 9.78 s, sys: 2.46 s, total: 12.2 s
Wall time: 12.6 s


In [ ]:
number_name_lookup["3/12 college"]

[4918991]

In [ ]:
%%time
def find_text_match(row):
    matching_ids = number_name_lookup.get(row.number_name)
    if len(matching_ids):
        match = parcels.loc[matching_ids]
        closest_parcel_id = match.distance(row.geometry).idxmin()
        row.LINZ_parcel_ID = closest_parcel_id
        row.addresses = match.addresses[closest_parcel_id]
        row.full_addresses = match.full_addresses[closest_parcel_id]
        row.LINZ_MATCH_CODE = 3
    return row
for year, df in tqdm(geocoding_results.items()):
    matches = df[pd.isna(df["LINZ_MATCH_CODE"]) & df.number_name.isin(number_name_lookup.keys())].progress_apply(find_text_match, axis=1)
    df.update(matches)

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/10234 [00:00<?, ?it/s]

  0%|          | 0/8025 [00:00<?, ?it/s]

  0%|          | 0/694 [00:00<?, ?it/s]

  0%|          | 0/376 [00:00<?, ?it/s]

CPU times: user 4min 53s, sys: 6.98 s, total: 5min
Wall time: 4min 59s


In [ ]:
for year, df in tqdm(geocoding_results.items()):
    df["Ranged_Address_indicator"] = df.full_address.str.contains('\d\w?\s?-', regex=True, na=False)
    df[df.Ranged_Address_indicator]
    print(f"{year}: {sum(df.Ranged_Address_indicator)} ranged addresses")

  0%|          | 0/4 [00:00<?, ?it/s]

2011: 407 ranged addresses
2014: 330 ranged addresses
2017: 242 ranged addresses
2021: 106 ranged addresses


In [ ]:
for year, df in tqdm(geocoding_results.items()):
    maybe_subdivision = df[df.number_name.str.contains("/") & pd.isna(df.LINZ_MATCH_CODE)].copy()
    if len(maybe_subdivision):
        maybe_subdivision.number_name = maybe_subdivision.number_name.str.split("/").str[-1]
        # step 1
        match = maybe_subdivision[~pd.isna(maybe_subdivision.addresses)].apply(check_match, axis=1)
        if len(match):
            maybe_subdivision["LINZ_MATCH_CODE"] = match
        else:
            maybe_subdivision["LINZ_MATCH_CODE"] = np.nan
        # step 2
        matches = maybe_subdivision[
            pd.isna(match) &
            maybe_subdivision.number_name.isin(number_name_lookup.keys())
        ].apply(find_match_in_range, axis=1)
        maybe_subdivision.update(matches)
        # step 3
        matches = maybe_subdivision[
            pd.isna(maybe_subdivision["LINZ_MATCH_CODE"]) & maybe_subdivision.number_name.isin(number_name_lookup.keys())
        ].apply(find_text_match, axis=1)
        maybe_subdivision.update(matches)
        maybe_subdivision.LINZ_MATCH_CODE = maybe_subdivision.LINZ_MATCH_CODE.replace({1: 4, 2: 5, 3: 6})
        df.update(maybe_subdivision)

    def strip_char(s):
        number, name = s.split()
        number = "".join([c for c in number if c.isnumeric()])
        return number + " " + name
    maybe_subdivision = df[
        df.number_name.str.contains("[0-9][a-zA-Z] ") &
        pd.isna(df.LINZ_MATCH_CODE)
    ].copy()
    if len(maybe_subdivision):
        maybe_subdivision.number_name = maybe_subdivision.number_name.apply(strip_char)
        # step 1
        match = maybe_subdivision[~pd.isna(maybe_subdivision.addresses)].apply(check_match, axis=1)
        if len(match):
            maybe_subdivision["LINZ_MATCH_CODE"] = match
        else:
            maybe_subdivision["LINZ_MATCH_CODE"] = np.nan
        # step 2
        matches = maybe_subdivision[
            pd.isna(match) &
            maybe_subdivision.number_name.isin(number_name_lookup.keys())
        ].apply(find_match_in_range, axis=1)
        maybe_subdivision.update(matches)
        # step 3
        matches = maybe_subdivision[
            pd.isna(maybe_subdivision["LINZ_MATCH_CODE"]) & maybe_subdivision.number_name.isin(number_name_lookup.keys())
        ].apply(find_text_match, axis=1)
        maybe_subdivision.update(matches)
        maybe_subdivision.LINZ_MATCH_CODE = maybe_subdivision.LINZ_MATCH_CODE.replace({1: 4, 2: 5, 3: 6})
        df.update(maybe_subdivision)

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
def check_street_match(row):
    if row.number_name and len(row.number_name)>1:
        street = row.number_name.split()[-1]
        if street in str(row.addresses):
            return 7
    return np.nan
for year, df in tqdm(geocoding_results.items()):
    street_matches = df[pd.isna(df.LINZ_MATCH_CODE)].progress_apply(check_street_match, axis=1)
    df.LINZ_MATCH_CODE.update(street_matches)

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/143116 [00:00<?, ?it/s]

  0%|          | 0/95283 [00:00<?, ?it/s]

  0%|          | 0/3056 [00:00<?, ?it/s]

  0%|          | 0/1421 [00:00<?, ?it/s]

In [ ]:
for year, df in tqdm(geocoding_results.items()):
    df.LINZ_MATCH_CODE[~pd.isna(df.LINZ_parcel_ID) & pd.isna(df.LINZ_MATCH_CODE)] = 8
    df.LINZ_MATCH_CODE.fillna(9, inplace=True)
    geocoding_results[year] = df

  0%|          | 0/4 [00:00<?, ?it/s]

<string>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<string>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<string>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<string>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [ ]:
for year, df in tqdm(geocoding_results.items()):
    print(year)
    display(df.LINZ_MATCH_CODE.value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


8.0    140704
1.0     27453
3.0     10234
7.0      2412
2.0      2171
6.0       705
5.0        32
4.0         1
Name: LINZ_MATCH_CODE, dtype: int64

2014


8.0    93417
1.0    21788
3.0     8025
2.0     1869
7.0     1866
6.0      644
5.0       32
4.0        2
Name: LINZ_MATCH_CODE, dtype: int64

2017


1.0    13349
8.0     2623
2.0     1545
3.0      694
6.0      464
7.0      433
5.0       25
4.0        3
Name: LINZ_MATCH_CODE, dtype: int64

2021


1.0    7078
8.0    1226
6.0     893
2.0     821
3.0     376
7.0     186
5.0      23
9.0       9
4.0       2
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
for year, df in tqdm(geocoding_results.items()):
    print(year)
    display(df.LINZ_MATCH_CODE[df.Ranged_Address_indicator].value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


8.0    306
7.0     51
1.0     49
3.0      1
Name: LINZ_MATCH_CODE, dtype: int64

2014


8.0    243
7.0     45
1.0     41
3.0      1
Name: LINZ_MATCH_CODE, dtype: int64

2017


8.0    187
7.0     36
1.0     19
Name: LINZ_MATCH_CODE, dtype: int64

2021


8.0    71
7.0    21
1.0    14
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
for year, df in tqdm(geocoding_results.items()):
    rvs[year].update(df)
    rvs[year]["geocoded_lat"] = df.lat
    rvs[year]["geocoded_lon"] = df.lon
    rvs[year]["geocoded_address"] = df.display_name
    distances = df[~pd.isna(df.LINZ_parcel_ID)].distance(parcels.loc[df.LINZ_parcel_ID[~pd.isna(df.LINZ_parcel_ID)]], align=False)
    rvs[year]["distance_to_parcel"] = distances
    rvs[year]["distance_to_parcel"] = rvs[year]["distance_to_parcel"].fillna(0)

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
for year, rv in tqdm(rvs.items()):
    rvs[year]["LINZ_MATCH_CODE"].fillna(9, inplace=True)

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
# Things which can't be geocoded
for addr in rv.full_address[(rv.LINZ_MATCH_CODE == 9) & ~pd.isna(rv.full_address)]:
    print(addr)

31 Manarini RD
148R Bader Dr
25S Kilkenny Dr
21AC Arimu Rd
66R Calluna Cres
454R Weymouth Rd
145R Pukaki Rd
51R Kimpton Rd
6 Rathfamham RD
20 Manarini RD
1W Manor Park
114/15 Hillside Rd
54 Ikara RD
190R Aviemore Dr
7 Kitea PL
9 Kaokao LANE
114/4 Hillside Rd
89R Retreat Dr
4A/4B Clyde Rd
6A Rossmay TR
702S Great South Rd
34/13 Index Pl
58 Manarini RD
12W Banbury Pl
9A/2 Parr Tce
42391 Great North Rd
12 Southridge RD
76 Manarini RD
5W Sparrow Pl
11W Challinor St
15 Te Ara Poutama Whanake
66R Charntay Ave
198W Sandspit Rd
32 Toanga PL
59/5 Neil Ave
62 Manarini RD
4ER Westholm Way
30/101 Hokonui Rd
114/7 Hillside Rd
421455A Great South RD
9 Te Ara Poutama Whanake
50 Manarini RD
140ER Flanagan Rd
6 Toanga PL
15A Rothschild TR
8 Rathfamham RD
10 Glann RD
13W Matuku Pl
13 Rigby DR
211W Finlayson Ave
40R Hill Rd
22W Riverlea Ave
75ER Maketu Rd
63W Yates Rd
196/2 Bleakhouse Rd
567/1 Glenfield RD
27R Maxwell Ave
13 Southridge RD
30/106 Hokonui Rd
137 Mount Wellington HW
40R Jellicoe Rd
11S Sunn

In [ ]:
for year, rv in tqdm(rvs.items()):
    print(year)
    display(rv.LINZ_MATCH_CODE.value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


0.0    313530
8.0    140704
1.0     27453
9.0     19227
3.0     10234
7.0      2412
2.0      2171
6.0       705
5.0        32
4.0         1
Name: LINZ_MATCH_CODE, dtype: int64

2014


0.0    372162
8.0     93417
9.0     29241
1.0     21788
3.0      8025
2.0      1869
7.0      1866
6.0       644
5.0        32
4.0         2
Name: LINZ_MATCH_CODE, dtype: int64

2017


0.0    528203
1.0     13349
8.0      2623
9.0      2597
2.0      1545
3.0       694
6.0       464
7.0       433
5.0        25
4.0         3
Name: LINZ_MATCH_CODE, dtype: int64

2021


0.0    580537
1.0      7078
9.0      2268
8.0      1226
6.0       893
2.0       821
3.0       376
7.0       186
5.0        23
4.0         2
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
for year, rv in tqdm(rvs.items()):
    print(sum((rv.number_of_matched_parcels == 0) & ~pd.isna(rv.LINZ_parcel_ID)))
    rv.loc[(rv.number_of_matched_parcels == 0) & ~pd.isna(rv.LINZ_parcel_ID), "number_of_matched_parcels"] = 1
    rv["One_to_many_matched_parcels"] = (rv.number_of_matched_parcels > 1).astype(int)
    rv["Many_to_one_matched_parcels"] = (~pd.isna(rv.LINZ_parcel_ID) & rv.LINZ_parcel_ID.duplicated(keep=False)).astype(int)
    rvs[year] = rv

  0%|          | 0/4 [00:00<?, ?it/s]

183712
127643
19136
10605


In [ ]:
rv

Valuation_Number_Roll  Valuation_Number_Assessment  \
0                        1281                        28200   
1                        3952                        52600   
2                       32200                        41117   
3                       34110                        16600   
4                       37301                        38303   
...                       ...                          ...   
593405                  32749                        19927   
593406                     16                  21230030110   
593407                    941                        39000   
593408                  31250                     12656736   
593409                  33351                        14054   

       Valuation_Number_Suffix  District_Code  Situation_Number  \
0                          NaN             14                20   
1                            B             14               789   
2                          NaN             14                16   
3                            B             14                39   
4                          NaN             14               143   
...                        ...            ...               ...   
593405                     NaN             14                 4   
593406                     NaN             14                76   
593407                     NaN             14                 6   
593408                     NaN             14                22   
593409                     NaN             14                36   

       Additional_Situation_Number      Situation_Name  \
0                              -26          Neville St   
1                              NaN            Beach Rd   
2                              NaN        Te Wharau Dr   
3                              NaN       Cliff View Dr   
4                              NaN      Great South RD   
...                            ...                 ...   
593405                         NaN        Carnelian Ct   
593406                         NaN  Stonefields Avenue   
593407                         NaN      Woods Ridge Rd   
593408                         NaN     Arran Point PDE   
593409                         NaN        Ceramic LANE   

                                       Legal_Description  Land_Area  \
0                                        Lot 1 DP 440011     0.5499   
1                                    UNIT B AU2 DP 83542     0.0000   
2                                        LOT 8 DP 196200     0.0853   
3              LOT 19 DP 39875 1/2 SH BG FLAT 2 DP 86384     0.0000   
4                                 Lot 3 DP 129805 1430m2     0.1430   
...                                                  ...        ...   
593405                                  LOT 27 DP 207011     0.0514   
593406  Lot 101 DP 466374 1138m2, Lot 40 DP 466374 123m2     0.0123   
593407                                   Lot 25 DP 82380     0.2070   
593408        Lot 2 DP 533517 7/120 Sh Lot 604 DP 501394     0.0176   
593409                                 Unit 48 DP 533897     0.0000   

       Property_Category  Ownership_Code  Current_Effective_Valuation_Date  \
0                   CRSB               2                           1062021   
1                 RF197B               1                           1062021   
2                 RD200B               1                           1062021   
3                 RF197B               0                           1062021   
4                    IVP               0                           1062021   
...                  ...             ...                               ...   
593405            RD200B               1                           1062021   
593406            RF201B               1                           1062021   
593407            RD200B               1                           1062021   
593408            RF201B               2                           1062021   
593409            RF201B               2          

In [ ]:
for year, rv in tqdm(rvs.items()):
    print(year)
    display(rv.One_to_many_matched_parcels.value_counts(dropna=False))
    display(rv.Many_to_one_matched_parcels.value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


0    481843
1     34626
Name: One_to_many_matched_parcels, dtype: int64

1    258681
0    257788
Name: Many_to_one_matched_parcels, dtype: int64

2014


...

0    490481
1     59455
Name: One_to_many_matched_parcels, dtype: int64

0    351046
1    198890
Name: Many_to_one_matched_parcels, dtype: int64

2021


0    521886
1     71524
Name: One_to_many_matched_parcels, dtype: int64

0    379332
1    214078
Name: Many_to_one_matched_parcels, dtype: int64

In [ ]:
for year, rv in tqdm(rvs.items()):
    rvs[year] = rv.merge(parcels[["addresses", "full_addresses"]], how="left", left_on="LINZ_parcel_ID", right_index=True)

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
def get_full_addr(row):
    try:
        return row.full_addresses[row.addresses.index(row.number_name)]
    except:
        return
for year, rv in tqdm(rvs.items()):
    rvs[year]["matched_address"] = rv.progress_apply(get_full_addr, axis=1)

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/516469 [00:00<?, ?it/s]

  0%|          | 0/529046 [00:00<?, ?it/s]

  0%|          | 0/549936 [00:00<?, ?it/s]

  0%|          | 0/593410 [00:00<?, ?it/s]

In [ ]:
rvs[2017]

Valuation_Number_Roll  Valuation_Number_Assessment  \
0                       38703                        44617   
1                       38703                        44618   
2                       38703                        44619   
3                       38703                        44621   
4                       38703                        44622   
...                       ...                          ...   
549931                   2390                        50700   
549932                   2400                        33400   
549933                   2400                        34500   
549934                   2400                        34900   
549935                   2400                        35500   

       Valuation_Number_Suffix  District_Code  Situation_Number  \
0                          NaN             14              84.0   
1                          NaN             14              82.0   
2                          NaN             14              80.0   
3                          NaN             14              22.0   
4                          NaN             14               NaN   
...                        ...            ...               ...   
549931                       B             14              33.0   
549932                     NaN             14              84.0   
549933                     NaN             14             106.0   
549934                     NaN             14             114.0   
549935                     NaN             14             126.0   

       Additional_Situation_Number Situation_Name  \
0                              NaN    REYNOLDS RD   
1                              NaN    REYNOLDS RD   
2                              NaN    REYNOLDS RD   
3                              NaN    REYNOLDS RD   
4                              NaN    REYNOLDS RD   
...                            ...            ...   
549931                           A  Ellerton Road   
549932                         NaN     Peary Road   
549933                         NaN     Peary Road   
549934                         NaN     Peary Road   
549935                         NaN       Peary RD   

                              Legal_Description  Land_Area Property_Category  \
0                               LOT 17 DP344916     0.0836            RD201B   
1                               LOT 18 DP344916     0.0829            RD200B   
2                               LOT 19 DP344916     0.0839            RD200B   
3                               LOT 21 DP344916     5.5664                OS   
4                               LOT 22 DP344916     1.7965                OP   
...                                         ...        ...               ...   
549931  Flat 2 DP 114220, Lot 1 DP 111459 938m2     0.0000            RD198B   
549932                    Lot 54 DP 20380 518m2     0.0518            RD192B   
549933                    Lot 43 DP 17805 822m2     0.0822            RD191B   
549934                    Lot 39 DP 17805 541m2     0.0541            RD192A   
549935                    Lot 33 DP 17805 557m2     0.0557            RD192B   

        Ownership_Code Current_Effective_Valuation_Date  Capital_Value  \
0                  1.0                       2014-07-01         860000   
1                  1.0                       2014-07-01         820000   
2                  1.0                       2014-07-01         820000   
3                  4.0                       2014-07-01        1080000   
4                  4.0                       2014-07-01         500000   
...                ...                              ...            ...   
549931             1.0                       2014-07-01        1475000   
549932             1.0                       2014-07-01        1360000   
549933             1.0                       2014-07-01        2000000   
549934             1.0                       2014-07-01        1650000   
549935             1.0                       2

In [ ]:
for year, rv in tqdm(rvs.items()):
    rv["Ranged_Address_indicator"] = rv.full_address.str.contains('\d\w?\s?-', regex=True, na=False)
    print(f"{year}: {sum(rv.Ranged_Address_indicator)} ranged addresses")

  0%|          | 0/4 [00:00<?, ?it/s]

2011: 3876 ranged addresses
2014: 3761 ranged addresses
2017: 3535 ranged addresses
2021: 3062 ranged addresses


In [ ]:
for year, rv in tqdm(rvs.items()):
    print(year)
    display(rv[rv.Ranged_Address_indicator].LINZ_MATCH_CODE.value_counts(dropna=False))

  0%|          | 0/4 [00:00<?, ?it/s]

2011


0.0    3413
8.0     306
9.0      56
7.0      51
1.0      49
3.0       1
Name: LINZ_MATCH_CODE, dtype: int64

2014


0.0    3386
8.0     243
9.0      45
7.0      45
1.0      41
3.0       1
Name: LINZ_MATCH_CODE, dtype: int64

2017


0.0    3258
8.0     187
7.0      36
9.0      35
1.0      19
Name: LINZ_MATCH_CODE, dtype: int64

2021


0.0    2938
8.0      71
7.0      21
9.0      18
1.0      14
Name: LINZ_MATCH_CODE, dtype: int64

In [ ]:
rvs[2017].keys()

Index(['Valuation_Number_Roll', 'Valuation_Number_Assessment',
       'Valuation_Number_Suffix', 'District_Code', 'Situation_Number',
       'Additional_Situation_Number', 'Situation_Name', 'Legal_Description',
       'Land_Area', 'Property_Category', 'Ownership_Code',
       'Current_Effective_Valuation_Date', 'Capital_Value',
       'Improvements_Value', 'Land_Value', 'Trees', 'REVISED_CAPITAL_VALUE',
       'REVISED_IMPROVEMENTS_VALUE', 'REVISED_LAND_VALUE', 'REVISED_TREES',
       'Improvements_Description', 'Certificate_of_Title',
       'Additional_Certificate_of_Title', 'Zoning', 'Actual_Property_Use',
       'Units_of_Use', 'Off_street_Parking', 'Building_Age_Indicator',
       'Building_Condition_Indicator', 'Building_Construction_Indicator',
       'Building_Site_Coverage', 'Building_Total_Floor_Area', 'Mass_Contour',
       'Mass_View', 'Mass_Scope_of_View', 'Mass_Total_Living_Area',
       'Mass_Deck', 'Mass_Workshop_Laundry', 'Mass_Other_Improvements',
       'Mass_Garage_

In [ ]:
%%time
phase0 = pd.read_csv("output/parcels_phase0.csv", index_col="LINZ_parcel_ID", low_memory=False, lineterminator="\n")
phase0

CPU times: user 12.6 s, sys: 1.57 s, total: 14.2 s
Wall time: 14.7 s


appellation affected_surveys     parcel_intent  \
LINZ_parcel_ID                                                            
4918991             Lot 327 DP 56341         DP 56341              DCDB   
4919914             Lot 178 DP 56342         DP 56342              DCDB   
4926734             Lot 144 DP 53562         DP 53562              DCDB   
4926945             Lot 183 DP 56342         DP 56342              DCDB   
4929034             Lot 260 DP 56341         DP 56341              DCDB   
...                              ...              ...               ...   
5227472                          NaN              NaN              Road   
5242816                          NaN              NaN              Road   
7520053              Lot 5 DP 465319        DP 465319  Fee Simple Title   
7520049              Lot 1 DP 465319        DP 465319  Fee Simple Title   
4733845         Part Lot 59 DP 60001         DP 60001              DCDB   

               topology_type  \
LINZ_parcel_ID                 
4918991              Primary   
4919914              Primary   
4926734              Primary   
4926945              Primary   
4929034              Primary   
...                      ...   
5227472              Primary   
5242816              Primary   
7520053              Primary   
7520049              Primary   
4733845              Primary   

                                                statutory_actions  \
LINZ_parcel_ID                                                      
4918991                                                       NaN   
4919914                                                       NaN   
4926734                                                       NaN   
4926945                                                       NaN   
4929034                                                       NaN   
...                                                           ...   
5227472                                                       NaN   
5242816                                                       NaN   
7520053                                                       NaN   
7520049                                                       NaN   
4733845         [Referenced] Declaration That State Housing La...   

                 land_district                                    titles  \
LINZ_parcel_ID                                                             
4918991         North Auckland                                  NA8C/911   
4919914         North Auckland                          474924, NA8C/768   
4926734         North Auckland  386353, 386354, 386355, 386356, NA4D/859   
4926945         North Auckland                          433646, NA8C/773   
4929034         North Auckland                          488577, NA8C/850   
...                        ...                                       ...   
5227472         North Auckland                                       NaN   
5242816         North Auckland                                       NaN   
7520053         North Auckland                                    621250   
7520049         North Auckland                                    619244   
4733845         North Auckland                                 NA86D/103   

                survey_area  calc_area  LINZ_parcel_centroid_lon  \
LINZ_parcel_ID                                                     
4918991               642.0      643.0                174.843218   
4919914               650.0      651.0                174.846572   
4926734               640.0      640.0                174.845299   
4926945               913.0      914.0                174.845585   
4929034               622.0      624.0                174.847627   
...                     ...        ...                       ...   
5227472                 NaN     1330.0                174.874361   
5242816                 NaN     1049.0                174.872269   
7520053              2253.0     2252.0                174.875600 

In [ ]:
for year, rv in tqdm(rvs.items()):
    rv = rv.merge(phase0, on="LINZ_parcel_ID", how="left")
    rv.to_csv(f"restricted/REVAL{year} Property Data Supply_augmented.csv", index=False)

  0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
rv[rv.LINZ_MATCH_CODE.between(1,8)].to_csv(f"restricted/REVAL{year} Property Data Supply_augmented_sample_geocoded.csv", index=False)